In [1]:
#  Copyright 2016 The TensorFlow Authors. All Rights Reserved.
#
#  Licensed under the Apache License, Version 2.0 (the "License");
#  you may not use this file except in compliance with the License.
#  You may obtain a copy of the License at
#
#   http://www.apache.org/licenses/LICENSE-2.0
#
#  Unless required by applicable law or agreed to in writing, software
#  distributed under the License is distributed on an "AS IS" BASIS,
#  WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
#  See the License for the specific language governing permissions and
#  limitations under the License.
"""Convolutional Neural Network Estimator for MNIST, built with tf.layers."""

from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)


def cnn_model_fn(features, labels, mode):
  """Model function for CNN."""
  # Input Layer
  # Reshape X to 4-D tensor: [batch_size, width, height, channels]
  # MNIST images are 28x28 pixels, and have one color channel
  input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

  # Convolutional Layer #1
  # Computes 32 features using a 5x5 filter with ReLU activation.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 28, 28, 1]
  # Output Tensor Shape: [batch_size, 28, 28, 32]
  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #1
  # First max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 28, 28, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 32]
  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

  # Convolutional Layer #2
  # Computes 64 features using a 5x5 filter.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 14, 14, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 64]
  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #2
  # Second max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 14, 14, 64]
  # Output Tensor Shape: [batch_size, 7, 7, 64]
  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

  # Flatten tensor into a batch of vectors
  # Input Tensor Shape: [batch_size, 7, 7, 64]
  # Output Tensor Shape: [batch_size, 7 * 7 * 64]
  pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])

  # Dense Layer
  # Densely connected layer with 1024 neurons
  # Input Tensor Shape: [batch_size, 7 * 7 * 64]
  # Output Tensor Shape: [batch_size, 1024]
  dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)

  # Add dropout operation; 0.6 probability that element will be kept
  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

  # Logits layer
  # Input Tensor Shape: [batch_size, 1024]
  # Output Tensor Shape: [batch_size, 10]
  logits = tf.layers.dense(inputs=dropout, units=10)

  predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }
  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

  # Calculate Loss (for both TRAIN and EVAL modes)
  loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

  # Configure the Training Op (for TRAIN mode)
  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

  # Add evaluation metrics (for EVAL mode)
  eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
  return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)


def main(unused_argv):
  # Load training and eval data
  mnist = tf.contrib.learn.datasets.load_dataset("mnist")
  train_data = mnist.train.images  # Returns np.array
  train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
  eval_data = mnist.test.images  # Returns np.array
  eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

  # Create the Estimator
  mnist_classifier = tf.estimator.Estimator(
      model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

  # Set up logging for predictions
  # Log the values in the "Softmax" tensor with label "probabilities"
  tensors_to_log = {"probabilities": "softmax_tensor"}
  logging_hook = tf.train.LoggingTensorHook(
      tensors=tensors_to_log, every_n_iter=50)

  # Train the model
  train_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": train_data},
      y=train_labels,
      batch_size=100,
      num_epochs=None,
      shuffle=True)
  mnist_classifier.train(
      input_fn=train_input_fn,
      steps=20000,
      hooks=[logging_hook])

  # Evaluate the model and print results
  eval_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": eval_data},
      y=eval_labels,
      num_epochs=1,
      shuffle=False)
  eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
  print(eval_results)


if __name__ == "__main__":
  tf.app.run()

Instructions for updating:
Please use tf.data.
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please write your own downloading logic.
Instructions for updating:
Please use urllib or similar directly.
Successfully downloaded train-images-idx3-ubyte.gz 9912422 bytes.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST-data/train-images-idx3-ubyte.gz
Successfully downloaded train-labels-idx1-ubyte.gz 28881 bytes.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Successfully downloaded t10k-images-idx3-ubyte.gz 1648877 bytes.
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Successfully downloaded t10k-labels-idx1-ubyte.gz 4542 bytes.
Extracting MNIST-data/t10k-labels-idx1-u

INFO:tensorflow:loss = 2.2941484, step = 1
INFO:tensorflow:probabilities = [[0.10203241 0.08867753 0.10704772 0.12505649 0.10081714 0.09707367
  0.08930179 0.06950844 0.11062922 0.10985555]
 [0.10784528 0.08583963 0.10910823 0.11382785 0.10554688 0.10069003
  0.09076705 0.08335468 0.10374921 0.09927115]
 [0.09971679 0.09313465 0.11356431 0.1093359  0.09798577 0.10066581
  0.09548134 0.09921124 0.09126598 0.0996383 ]
 [0.11274736 0.0960783  0.11476704 0.11174918 0.09272759 0.08791702
  0.09701023 0.09201919 0.10169926 0.0932849 ]
 [0.09756199 0.09973842 0.1152217  0.11425339 0.09250822 0.08655869
  0.09249373 0.09127028 0.10740528 0.10298826]
 [0.10007719 0.09545127 0.11910959 0.11090211 0.10128473 0.09940658
  0.08411086 0.08591924 0.10333192 0.10040655]
 [0.10732575 0.09784158 0.10325681 0.10610545 0.08740425 0.10407889
  0.09815866 0.08812419 0.10054298 0.1071614 ]
 [0.10272969 0.08764459 0.1173617  0.10572318 0.10194036 0.0951785
  0.08501808 0.09613461 0.11003879 0.09823052]
 [0.10

INFO:tensorflow:global_step/sec: 6.90209
INFO:tensorflow:probabilities = [[0.10806239 0.09037527 0.11414803 0.11293502 0.09440766 0.09049474
  0.10344339 0.08579975 0.10316216 0.09717165]
 [0.10419795 0.09820447 0.11342478 0.11088431 0.10234754 0.09003198
  0.08962739 0.09081622 0.09771236 0.10275294]
 [0.11877377 0.08789495 0.10629109 0.12577453 0.09764241 0.09262565
  0.09722036 0.07961075 0.10144285 0.09272361]
 [0.09760596 0.09701391 0.11441061 0.10678609 0.09889995 0.09961011
  0.09312119 0.09465798 0.09242282 0.10547136]
 [0.12183671 0.09742034 0.12050188 0.10884878 0.09801796 0.08382852
  0.09354683 0.07277442 0.10592388 0.09730072]
 [0.10627264 0.0905107  0.11337335 0.10468014 0.10497484 0.08277782
  0.08893232 0.09087743 0.11307085 0.10452987]
 [0.10610102 0.08657565 0.11770479 0.11528605 0.10775056 0.08976809
  0.09678391 0.08069538 0.11167806 0.08765648]
 [0.11483474 0.07601779 0.12418632 0.12844792 0.09633046 0.09101616
  0.08952662 0.08017293 0.09800841 0.10145868]
 [0.099

INFO:tensorflow:loss = 2.2802408, step = 101 (14.489 sec)
INFO:tensorflow:probabilities = [[0.10993744 0.08373905 0.12428304 0.0922654  0.10476504 0.08956379
  0.0847069  0.08698429 0.10771672 0.11603825]
 [0.10861907 0.09637281 0.10976271 0.11104837 0.08977557 0.09449646
  0.10017064 0.08796979 0.10113595 0.10064861]
 [0.11325275 0.08972237 0.11428998 0.10468363 0.10037561 0.09694324
  0.09186425 0.09380629 0.09699844 0.09806349]
 [0.10573868 0.08470797 0.11036868 0.09732065 0.10409201 0.10068098
  0.09334695 0.1059055  0.09954277 0.09829578]
 [0.1007551  0.08784066 0.11716606 0.09687575 0.10282371 0.08135387
  0.09110918 0.0981895  0.10844807 0.11543811]
 [0.10214977 0.09457627 0.1041778  0.10256386 0.09602891 0.09316112
  0.08977436 0.095735   0.11667924 0.1051537 ]
 [0.09779073 0.09597321 0.1044064  0.11846813 0.10106339 0.10656072
  0.08289479 0.09054121 0.10548822 0.09681323]
 [0.11469211 0.08275041 0.11849843 0.11044309 0.08726624 0.09959625
  0.09329793 0.08703593 0.10676126 0.

INFO:tensorflow:global_step/sec: 6.99027
INFO:tensorflow:probabilities = [[0.10151429 0.08607038 0.10897635 0.11709971 0.0926139  0.09780709
  0.09188581 0.10407437 0.10425024 0.09570785]
 [0.10709166 0.09103059 0.10883776 0.09860826 0.09922953 0.09949137
  0.09956038 0.09795974 0.09847011 0.09972059]
 [0.11318488 0.09576479 0.1082653  0.10692351 0.09409542 0.08279965
  0.10340337 0.09510986 0.10907049 0.09138276]
 [0.09914181 0.09404089 0.11431149 0.10246825 0.09937891 0.10219114
  0.08868872 0.09558219 0.09675808 0.10743851]
 [0.10249498 0.09268662 0.12465848 0.11000717 0.08697854 0.09301626
  0.08958784 0.08860449 0.10495855 0.10700708]
 [0.11291116 0.08629851 0.10994834 0.08928507 0.1032912  0.08552319
  0.08819062 0.10306837 0.10745911 0.11402451]
 [0.10437797 0.09407251 0.11470646 0.10510367 0.09500466 0.09367346
  0.09838865 0.09041647 0.09657621 0.10768002]
 [0.11943007 0.08848322 0.1080498  0.10548793 0.09888432 0.08881483
  0.09679669 0.09658226 0.09759529 0.09987559]
 [0.093

...

INFO:tensorflow:global_step/sec: 6.94912
INFO:tensorflow:probabilities = [[0.00000031 0.00000651 0.00016147 0.00037027 0.00000028 0.00000331
  0.         0.99909735 0.00001088 0.00034967]
 [0.99981695 0.         0.00011854 0.00000003 0.00000007 0.00000016
  0.00001102 0.0000001  0.00005269 0.00000042]
 [0.00008529 0.02071587 0.00283715 0.01479186 0.00089828 0.93207604
  0.00597835 0.00392478 0.01856929 0.00012307]
 [0.0000181  0.00000189 0.00024455 0.00000306 0.83755064 0.00146462
  0.1361412  0.00005629 0.00706152 0.0174581 ]
 [0.00001176 0.9992835  0.00009187 0.0000442  0.00000501 0.00001478
  0.00000291 0.00004392 0.00046858 0.0000335 ]
 [0.00002016 0.00236318 0.00185347 0.00775583 0.76297283 0.00029989
  0.00012823 0.0019326  0.0164597  0.20621407]
 [0.00121541 0.00004406 0.00230827 0.0018267  0.00005103 0.00019824
  0.00000001 0.9600537  0.00245311 0.03184945]
 [0.00000716 0.00000003 0.00000066 0.00090194 0.         0.99906904
  0.00000003 0.         0.00001896 0.00000219]
 [0.000

INFO:tensorflow:loss = 0.08431632, step = 19901 (14.389 sec)
INFO:tensorflow:probabilities = [[0.00000298 0.00042874 0.00000557 0.00011396 0.8439561  0.00002548
  0.00000841 0.00062582 0.00030801 0.15452488]
 [0.0000082  0.00022713 0.00164502 0.99265033 0.00000007 0.00536716
  0.00000215 0.00001141 0.00008444 0.00000407]
 [0.00021773 0.00003992 0.0000424  0.00155052 0.00029461 0.01044653
  0.98307174 0.00000244 0.00429762 0.00003647]
 [0.9629373  0.0000007  0.00003954 0.00001751 0.00000073 0.03294707
  0.00401364 0.00001285 0.00001987 0.00001091]
 [0.00096222 0.00005093 0.03004025 0.00335973 0.00782255 0.00058789
  0.0005574  0.00076328 0.6632943  0.2925615 ]
 [0.0000718  0.99587005 0.0009316  0.00049449 0.00018188 0.00000417
  0.00038901 0.00045191 0.00158038 0.00002473]
 [0.9999801  0.         0.00000509 0.0000003  0.00000004 0.00001057
  0.00000274 0.0000005  0.00000032 0.00000038]
 [0.00000045 0.00000002 0.00000221 0.00000001 0.99898726 0.00002058
  0.00009692 0.0000502  0.00027348

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.058835227.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2018-11-08-03:19:16
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model/model.ckpt-20000
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-11-08-03:19:21
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9688, global_step = 20000, loss = 0.10353494
INFO:tensorflow:Saving 'checkpoint_path' summary for global step 20000: /tmp/mnist_convnet_model/model.ckpt-20000
{'accuracy': 0.9688, 'loss': 0.10353494, 'global_step': 20000}


SystemExit: 

/usr/local/lib/python3.6/dist-packages/IPython/core/interactiveshell.py:3273: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
